In [1]:
ACCESS_KEY = "" # your access key
SECRET_KEY = "" # your secret key
ENCODED_SECRET_KEY = SECRET_KEY.replace("/", "%2F")
AWS_BUCKET_NAME = "comp4651-project-data"
MOUNT_NAME = "data"

#dbutils.fs.mount("s3a://%s:%s@%s" % (ACCESS_KEY, ENCODED_SECRET_KEY, AWS_BUCKET_NAME), "/mnt/%s" % MOUNT_NAME)
display(dbutils.fs.ls("/mnt/%s" % MOUNT_NAME))

#val mdf = spark.read.option("multiline", "true").json("train.json")
#mdf.show(false)

#df = spark.read.text("/mnt/%s/test.json" % MOUNT_NAME)

path name size dbfs:/mnt/data/oregon-prod/ oregon-prod/ 0 dbfs:/mnt/data/parsed_df.csv/ parsed_df.csv/ 0 dbfs:/mnt/data/test.json test.json 2844086 dbfs:/mnt/data/train.json train.json 12415067

In [2]:
display(dbutils.fs.ls("/mnt/%s" % MOUNT_NAME))

path name size dbfs:/mnt/data/oregon-prod/ oregon-prod/ 0 dbfs:/mnt/data/parsed_df.csv/ parsed_df.csv/ 0 dbfs:/mnt/data/test.json test.json 2844086 dbfs:/mnt/data/train.json train.json 12415067

In [3]:
df = spark.read.option("multiline", "true").json("dbfs:/mnt/data/train.json")
display(df)

cuisine id ingredients greek 10259 List(romaine lettuce, black olives, grape tomatoes, garlic, pepper, purple onion, seasoning, garbanzo beans, feta cheese crumbles) southern_us 25693 List(plain flour, ground pepper, salt, tomatoes, ground black pepper, thyme, eggs, green tomatoes, yellow corn meal, milk, vegetable oil) filipino 20130 List(eggs, pepper, salt, mayonaise, cooking oil, green chilies, grilled chicken breasts, garlic powder, yellow onion, soy sauce, butter, chicken livers) indian 22213 List(water, vegetable oil, wheat, salt) indian 13162 List(black pepper, shallots, cornflour, cayenne pepper, onions, garlic paste, milk, butter, salt, lemon juice, water, chili powder, passata, oil, ground cumin, boneless chicken skinless thigh, garam masala, double cream, natural yogurt, bay leaf) jamaican 6602 List(plain flour, sugar, butter, eggs, fresh ginger root, salt, ground cinnamon, milk, vanilla extract, ground ginger, powdered sugar, baking powder) spanish 42779 List(olive oil, salt, medium shrimp, pepper, garlic, chopped cilantro, jalapeno chilies, flat leaf parsley, skirt steak, white vinegar, sea salt, bay leaf, chorizo sausage) italian 3735 List(sugar, pistachio nuts, white almond bark, flour, vanilla extract, olive oil, almond extract, eggs, baking powder, dried cranberries) mexican 16903 List(olive oil, purple onion, fresh pineapple, pork, poblano peppers, corn tortillas, cheddar cheese, ground black pepper, salt, iceberg lettuce, lime, jalapeno chilies, chopped cilantro fresh) italian 12734 List(chopped tomatoes, fresh basil, garlic, extra-virgin olive oil, kosher salt, flat leaf parsley) italian 5875 List(pimentos, sweet pepper, dried oregano, olive oil, garlic, sharp cheddar cheese, pepper, swiss cheese, provolone cheese, canola oil, mushrooms, black olives, sausages) chinese 45887 List(low sodium soy sauce, fresh ginger, dry mustard, green beans, white pepper, sesame oil, scallions, canola oil, sugar, Shaoxing wine, garlic, ground turkey, water, crushed red pepper flakes, corn starch) italian 2698 List(Italian parsley leaves, walnuts, hot red pepper flakes, extra-virgin olive oil, fresh lemon juice, trout fillet, garlic cloves, chipotle chile, fine sea salt, flat leaf parsley) mexican 41995 List(ground cinnamon, fresh cilantro, chili powder, ground coriander, kosher salt, ground black pepper, garlic, plum tomatoes, avocado, lime juice, flank steak, salt, ground cumin, black pepper, olive oil, crushed red pepper flakes, onions) italian 31908 List(fresh parmesan cheese, butter, all-purpose flour, fat free less sodium chicken broth, chopped fresh chives, gruyere cheese, ground black pepper, bacon slices, gnocchi, fat free milk, cooking spray, salt) indian 24717 List(tumeric, vegetable stock, tomatoes, garam masala, naan, red lentils, red chili peppers, onions, spinach, sweet potatoes) british 34466 List(greek yogurt, lemon curd, confectioners sugar, raspberries) italian 1420 List(italian seasoning, broiler-fryer chicken, mayonaise, zesty italian dressing) thai 2941 List(sugar, hot chili, asian fish sauce, lime juice) vietnamese 8152 List(soy sauce, vegetable oil, red bell pepper, chicken broth, yellow squash, garlic chili sauce, sliced green onions, broccolini, salt, fresh lime juice, cooked rice, chicken breasts, corn starch) thai 13121 List(pork loin, roasted peanuts, chopped cilantro fresh, hoisin sauce, creamy peanut butter, chopped fresh mint, thai basil, rice, medium shrimp, water, rice noodles, beansprouts) mexican 40523 List(roma tomatoes, kosher salt, purple onion, jalapeno chilies, lime, chopped cilantro) southern_us 40989 List(low-fat mayonnaise, pepper, salt, baking potatoes, eggs, spicy brown mustard) chinese 29630 List(sesame seeds, red pepper, yellow peppers, water, extra firm tofu, broccoli, soy sauce, orange bell pepper, arrowroot powder, fresh ginger, sesame oil, red curry paste) italian 49136 List(marinara sauce, flat leaf parsley, olive oil, linguine, capers, crushed red pepper flakes, olives, le

In [4]:
# occur = rdd.flatMap(lambda (cuisine,_,ingredients): [(cuisine, ing) for ing in ingredients])
# occur.collect()
# freq=occur.map(lambda (cuisine,ingredient): ((cuisine,ingredient),1)).reduce(lambda x,y:x+y)
# freq.collect()

In [5]:
# get the cuisine dictionary
cuisine_list = df.select('cuisine').distinct().collect() # list'
cuisines = [row['cuisine'] for row in cuisine_list]
cuisine_dict = {}
for i,cuisine in enumerate(cuisines):
  cuisine_dict[cuisine] = i

print(cuisine_dict)

{u'irish': 17, u'mexican': 9, u'filipino': 14, u'chinese': 11, u'vietnamese': 7, u'moroccan': 16, u'brazilian': 19, u'japanese': 18, u'french': 6, u'greek': 1, u'indian': 4, u'cajun_creole': 0, u'british': 13, u'spanish': 5, u'russian': 2, u'jamaican': 12, u'korean': 3, u'southern_us': 15, u'thai': 10, u'italian': 8}

In [6]:
# get the cuisine dictionary

occur = df.rdd.flatMap(lambda (cuisine,_,ingredients): [(cuisine, ing) for ing in ingredients])
occur = occur.map(lambda (cuisine, ing): (ing, 1)).reduceByKey(lambda a,b: a+b)
ingredient_list = occur.collect()

ingredients = [row[0] for row in ingredient_list]
ingredient_dict = {}
for i,ingredient in enumerate(ingredients):
  ingredient_dict[ingredient] = i

# print(ingredient_dict)

In [7]:
tuple_length = len(ingredient_dict) + 1 # 1 for the cuisine/label
def parseRow(row):
  cuisine, ingredients = row[0], row[2]
  one_positions = [ingredient_dict[ing] for ing in ingredients]
  row_vals = [0] * tuple_length
  for one in one_positions:
    row_vals[one] = 1
  row_vals[-1] = cuisine_dict[cuisine]
  return tuple(row_vals)

vals = df.rdd.map(parseRow).collect()

In [8]:
(sample_df, _) = df.randomSplit([0.0001,0.9999],1900009193L) # sample_df.count()=4
sample_vals = sample_df.rdd.map(parseRow).collect()
# display(sample_df)
# for key, value in cuisine_dict.items():
#   if value == sample_vals[0][-1]:
#     print(key)
  
# for ing in ["capers","eggplant","chopped fresh thyme","olive oil","marinara sauce","chopped garlic","vegetable oil cooking spray","zucchini","onions","fresh basil","monkfish fillets","bell pepper"]:
#   print(sample_vals[0][ingredient_dict[ing]])

In [9]:
from pyspark.sql import SQLContext
sqlContext = SQLContext(sc)

columns = map(str, range(0, len(ingredients)+1))
parsed_df = sqlContext.createDataFrame(vals, columns)
#parsed_df = sqlContext.createDataFrame(sample_vals, columns)
display(parsed_df)

0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 278 279 280 281 282 283 284 285 286 287 288 289 290 291 292 293 294 295 296 297 298 299 300 301 302 303 304 305 306 307 308 309 310 311 312 313 314 315 316 317 318 319 320 321 322 323 324 325 326 327 328 329 330 331 332 333 334 335 336 337 338 339 340 341 342 343 344 345 346 347 348 349 350 351 352 353 354 355 356 357 358 359 360 361 362 363 364 365 366 367 368 369 370 371 372 373 374 375 376 377 378 379 380 381 382 383 384 385 386 387 388 389 390 391 392 393 394 395 396 397 398 399 400 401 402 403 404 405 406 407 408 409 410 411 412 413 414 415 416 417 418 419 420 421 422 423 424 425 426 427 428 429 430 431 432 433 434 435 436 437 438 439 440 441 442 443 444 445 446 447 448 449 450 451 452 453 454 455 456 457 458 459 460 461 462 463 464 465 466 467 468 469 470 471 472 473 474 475 476 477 478 479 480 481 482 483 484 485 486 487 488 489 490 491 492 493 494 495 496 497 498 499 500 501 502 503 504 505 506 507 508 509 510 511 512 513 514 515 516 517 518 519 520 521 522 523 524 525 526 527 528 529 530 531 532 533 534 535 536 537 538 539 540 541 542 543 544 545 546 547 548 549 550 551 552 553 554 555 556 557 558 559 560 561 562 563 564 565 566 567 568 569 570 571 572 573 574 575 576 577 578 579 580 581 582 583 584 585 586 587 588 589 590 591 592 593 594 595 596 597 598 599 600 601 602 603 604 605 606 607 608 609 610 611 612 613 614 615 616 617 618 619 620 621 622 623 624 625 626 627 628 629 630 631 632 633 634 635 636 637 638 639 640 641 642 643 644 645 646 647 648 649 650 651 652 653 654 655 656 657 658 659 660 661 662 663 664 665 666 667 668 669 670 671 672 673 674 675 676 677 678 679 680 681 682 683 684 685 686 687 688 689 690 691 692 693 694 695 696 697 698 699 700 701 702 703 704 705 706 707 708 709 710 711 712 713 714 715 716 717 718 719 720 721 722 723 724 725 726 727 728 729 730 731 732 733 734 735 736 737 738 739 740 741 742 743 744 745 746 747 748 749 750 751 752 753 754 755 756 757 758 759 760 761 762 763 764 765 766 767 768 769 770 771 772 773 774 775 776 777 778 779 780 781 782 783 784 785 786 787 788 789 790 791 792 793 794 795 796 797 798 799 800 801 802 803 804 805 806 807 808 809 810 811 812 813 814 815 816 817 818 819 820 821 822 823 824 825 826 827 828 829 830 831 832 833 834 835 836 837 838 839 840 841 842 843 844 845 846 847 848 849 850 851 852 853 854 855 856 857 858 859 860 861 862 863 864 865 866 867 868 869 870 871 872 873 874 875 876 877 878 879 880 881 882 883 884 885 886 887 888 889 890 891 892 893 894 895 896 897 898 899 900 901 902 903 904 905 906 907 908 909 910 911 912 913 914 915 916 917 918 919 920 921 922 923 924 925 926 927 928 929 930 931 932 933 934 935 936 937 938 939 940 941 942 943 944 945 946 947 948 949 950 951 952 953 954 955 956 957 958 959 960 961 962 963 964 965 966 967 968 969 970 971 972 973 974 975 976 977 978 979 980 981 982 983 984 985 986 987 988 989 990 991 992 993 994 995 996 997 998 999 1000 1001 1002 1003 1004 1005 1006 1007 1008 1009 1010 1011 1012 1013 1014 1015 1016 1017 1018 1019 1020 1021 

In [10]:
parsed_df.write.save('/mnt/data/parsed_df.csv', format='csv', header=True, mode="overwrite")

In [11]:
parsed_df=df = spark.read.option("multiline", "true").json("dbfs:/mnt/data/train.json")

In [12]:
(split15DF, split85DF) = parsed_df.randomSplit([0.15,0.85],1900009193L)
testSetDF = split15DF.cache()
trainingSetDF = split85DF.cache()

In [13]:
parsed_df.printSchema()

root
-- 0: long (nullable = true)
-- 1: long (nullable = true)
-- 2: long (nullable = true)
-- 3: long (nullable = true)
-- 4: long (nullable = true)
-- 5: long (nullable = true)
-- 6: long (nullable = true)
-- 7: long (nullable = true)
-- 8: long (nullable = true)
-- 9: long (nullable = true)
-- 10: long (nullable = true)
-- 11: long (nullable = true)
-- 12: long (nullable = true)
-- 13: long (nullable = true)
-- 14: long (nullable = true)
-- 15: long (nullable = true)
-- 16: long (nullable = true)
-- 17: long (nullable = true)
-- 18: long (nullable = true)
-- 19: long (nullable = true)
-- 20: long (nullable = true)
-- 21: long (nullable = true)
-- 22: long (nullable = true)
-- 23: long (nullable = true)
-- 24: long (nullable = true)
-- 25: long (nullable = true)
-- 26: long (nullable = true)
-- 27: long (nullable = true)
-- 28: long (nullable = true)
-- 29: long (nullable = true)
-- 30: long (nullable = true)
-- 31: long (nullable = true)
-- 32: long (nullable = true)
-- 33: long (nullable = true)
-- 34: long (nullable = true)
-- 35: long (nullable = true)
-- 36: long (nullable = true)
-- 37: long (nullable = true)
-- 38: long (nullable = true)
-- 39: long (nullable = true)
-- 40: long (nullable = true)
-- 41: long (nullable = true)
-- 42: long (nullable = true)
-- 43: long (nullable = true)
-- 44: long (nullable = true)
-- 45: long (nullable = true)
-- 46: long (nullable = true)
-- 47: long (nullable = true)
-- 48: long (nullable = true)
-- 49: long (nullable = true)
-- 50: long (nullable = true)
-- 51: long (nullable = true)
-- 52: long (nullable = true)
-- 53: long (nullable = true)
-- 54: long (nullable = true)
-- 55: long (nullable = true)
-- 56: long (nullable = true)
-- 57: long (nullable = true)
-- 58: long (nullable = true)
-- 59: long (nullable = true)
-- 60: long (nullable = true)
-- 61: long (nullable = true)
-- 62: long (nullable = true)
-- 63: long (nullable = true)
-- 64: long (nullable = true)
-- 65: long (nullable = true)
-- 66: long (nullable = true)
-- 67: long (nullable = true)
-- 68: long (nullable = true)
-- 69: long (nullable = true)
-- 70: long (nullable = true)
-- 71: long (nullable = true)
-- 72: long (nullable = true)
-- 73: long (nullable = true)
-- 74: long (nullable = true)
-- 75: long (nullable = true)
-- 76: long (nullable = true)
-- 77: long (nullable = true)
-- 78: long (nullable = true)
-- 79: long (nullable = true)
-- 80: long (nullable = true)
-- 81: long (nullable = true)
-- 82: long (nullable = true)
-- 83: long (nullable = true)
-- 84: long (nullable = true)
-- 85: long (nullable = true)
-- 86: long (nullable = true)
-- 87: long (nullable = true)
-- 88: long (nullable = true)
-- 89: long (nullable = true)
-- 90: long (nullable = true)
-- 91: long (nullable = true)
-- 92: long (nullable = true)
-- 93: long (nullable = true)
-- 94: long (nullable = true)
-- 95: long (nullable = true)
-- 96: long (nullable = true)
-- 97: long (nullable = true)
-- 98: long (nullable = true)
-- 99: long (nullable = true)
-- 100: long (nullable = true)
-- 101: long (nullable = true)
-- 102: long (nullable = true)
-- 103: long (nullable = true)
-- 104: long (nullable = true)
-- 105: long (nullable = true)
-- 106: long (nullable = true)
-- 107: long (nullable = true)
-- 108: long (nullable = true)
-- 109: long (nullable = true)
-- 110: long (nullable = true)
-- 111: long (nullable = true)
-- 112: long (nullable = true)
-- 113: long (nullable = true)
-- 114: long (nullable = true)
-- 115: long (nullable = true)
-- 116: long (nullable = true)
-- 117: long (nullable = true)
-- 118: long (nullable = true)
-- 119: long (nullable = true)
-- 120: long (nullable = true)
-- 121: long (nullable = true)
-- 122: long (nullable = true)
-- 123: long (nullable = true)
-- 124: long (nullable = true)
-- 125: long (nullable = true)
-- 126: long (nullable = true)
-- 127: long (nullable = true)
-- 128: long (nullable = true)
-- 129: long (nullable = true)
-- 130: long (nullable = true)
-- 131: long (nullable = true)
-- 132: long 

In [14]:
from pyspark.ml.feature import VectorAssembler
vectorizer = VectorAssembler()
vectorizer.setInputCols(columns[:-2])
vectorizer.setOutputCol("features")

Out[ 14 ]: VectorAssembler_406184fd241637af96f9

In [15]:
from pyspark.ml.regression import DecisionTreeRegressor
from pyspark.ml import Pipeline

# Create a DecisionTreeRegressor
dt = DecisionTreeRegressor()

dt.setPredictionCol("Prediction_cuisine")\
  .setLabelCol("6714")\
  .setFeaturesCol("features")\
  .setMaxBins(100)

# Create a Pipeline
dtPipeline = Pipeline()

# Set the stages of the Pipeline
dtPipeline.setStages([vectorizer,dt])

# Let's first train on the entire dataset to see what we get
dtModel = dtPipeline.fit(trainingSetDF)

In [16]:
resultsDtDf = dtModel.transform(testSetDF)
resultsDtDf.write.save('/mnt/data/resultsDtDf.parquet', format='parquet', header=True, mode="overwrite")

In [17]:
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import RegressionEvaluator

# Create an RMSE evaluator using the label and predicted columns
regEval = RegressionEvaluator(predictionCol="Prediction_cuisine", labelCol="6714", metricName="rmse")

# We can reuse the RegressionEvaluator, regEval, to judge the model based on the best Root Mean Squared Error
# Let's create our CrossValidator with 3 fold cross validation
crossval = CrossValidator(estimator=dtPipeline, evaluator=regEval, numFolds=3)

# Let's tune over our dt.maxDepth parameter on the values 2 and 3, create a paramter grid using the ParamGridBuilder
paramGrid = (ParamGridBuilder()
             .addGrid(dt.maxDepth, [2,3])
             .build())

# Add the grid to the CrossValidator
crossval.setEstimatorParamMaps(paramGrid)

# Now let's find and return the best model
dtModelBest = crossval.fit(trainingSetDF).bestModel

In [18]:
# Now let's use dtModel to compute an evaluation metric for our test dataset: testSetDF
resultsBestDtDf = dtModelBest.transform(testSetDF)
resultsBestDtDf.write.save('/mnt/data/resultsBestDtDf.parquet', format='parquet', header=True, mode="overwrite")

In [20]:
from pyspark.ml.regression import RandomForestRegressor

# Create a RandomForestRegressor
rf = RandomForestRegressor()

rf.setPredictionCol("Prediction_cuisine")\
  .setLabelCol("6714")\
  .setFeaturesCol("features")\
  .setSeed(190088121L)\
  .setMaxDepth(8)\
  .setNumTrees(25)

# Create a Pipeline
rfPipeline = Pipeline()

# Set the stages of the Pipeline
rfPipeline.setStages([vectorizer, rf])

# Let's first train on the entire dataset to see what we get
rfModel = rfPipeline.fit(trainingSetDF)

In [21]:
resultsRfDf = rfModel.transform(testSetDF)
resultsRfDf.write.save('/mnt/data/resultsRfDf.parquet', format='parquet', header=True, mode="overwrite")

In [22]:
# Let's just reuse our CrossValidator with the new rfPipeline,  RegressionEvaluator regEval, and 3 fold cross validation
crossval.setEstimator(rfPipeline)

# Let's tune over our rf.maxBins parameter on the values 50 and 100, create a paramter grid using the ParamGridBuilder
paramGrid = (ParamGridBuilder()
             .addGrid(rf.maxBins, [50,100])
             .build())

# Add the grid to the CrossValidator
crossval.setEstimatorParamMaps(paramGrid)

# Now let's find and return the best model
rfModelBest = crossval.fit(trainingSetDF).bestModel

In [23]:
resultsBestRfDf = rfModelBest.transform(testSetDF)
resultsBestRfDf.write.save('/mnt/data/resultsBestRfDf.parquet', format='parquet', header=True, mode="overwrite")